In [21]:
from __future__ import division, print_function, absolute_import

import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split

In [22]:
twentyng_data = fetch_20newsgroups(subset='all')#,remove=('headers','footers','quotes'))
vectorizer = TfidfVectorizer(stop_words='english',max_df=0.95,min_df=2)
twentyng_data_vectors = vectorizer.fit_transform(twentyng_data.data)
print(twentyng_data_vectors.shape)
twentyng_target = twentyng_data.target
best = SelectKBest(chi2,1000)
twentyng_data_vectors = best.fit_transform(twentyng_data_vectors,twentyng_target)
tNGX_train = twentyng_data_vectors[15000:]
tNGX_test = twentyng_data_vectors[:15000]
tNGy_train = twentyng_target[15000:]
tNGy_test = twentyng_target[:15000]
# tNGX_train, tNGX_test, tNGy_train, tNGy_test = train_test_split(twentyng_data_vectors, twentyng_target, test_size=0.10, random_state=42)

(18846, 75562)


In [23]:
# Training Parameters
learning_rate = 0.01
num_steps = 1000
batch_size = 250

display_step = 100
examples_to_show = 10

# Network Parameters
num_hidden_1 = 200 # 1st layer num features
num_hidden_2 = 300 # 2nd layer num features (the latent dim)
num_input = 1000# 

# tf Graph input 
X = tf.placeholder("float", [None, num_input])

weights = {
    'encoder_h1': tf.Variable(tf.random_normal([num_input, num_hidden_1])),
    'encoder_h2': tf.Variable(tf.random_normal([num_hidden_1, num_hidden_2])),
    'decoder_h1': tf.Variable(tf.random_normal([num_hidden_2, num_hidden_1])),
    'decoder_h2': tf.Variable(tf.random_normal([num_hidden_1, num_input])),
}
biases = {
    'encoder_b1': tf.Variable(tf.random_normal([num_hidden_1])),
    'encoder_b2': tf.Variable(tf.random_normal([num_hidden_2])),
    'decoder_b1': tf.Variable(tf.random_normal([num_hidden_1])),
    'decoder_b2': tf.Variable(tf.random_normal([num_input])),
}

In [24]:
# Building the encoder
def encoder(x):
    # Encoder Hidden layer with sigmoid activation #1
    layer_1 = tf.nn.sigmoid(tf.add(tf.matmul(x, weights['encoder_h1']),
                                   biases['encoder_b1']))
    # Encoder Hidden layer with sigmoid activation #2
#     layer_2 = tf.nn.sigmoid(tf.add(tf.matmul(layer_1, weights['encoder_h2']),
#                                    biases['encoder_b2']))
    return layer_1


# Building the decoder
def decoder(x):
    # Decoder Hidden layer with sigmoid activation #1
#     layer_1 = tf.nn.sigmoid(tf.add(tf.matmul(x, weights['decoder_h1']),
#                                    biases['decoder_b1']))
    # Decoder Hidden layer with sigmoid activation #2
    layer_2 = tf.nn.sigmoid(tf.add(tf.matmul(x, weights['decoder_h2']),
                                   biases['decoder_b2']))
    return layer_2

# Construct model
encoder_op = encoder(X)
decoder_op = decoder(encoder_op)

# Prediction
y_pred = decoder_op
# Targets (Labels) are the input data.
y_true = X

# Define loss and optimizer, minimize the squared error
loss = tf.reduce_mean(tf.pow(y_true - y_pred, 2))
optimizer = tf.train.AdamOptimizer().minimize(loss)
#optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)

# Initialize the variables (i.e. assign their default value)
init = tf.global_variables_initializer()

In [25]:
sess = tf.Session()
sess.run(init)

hm_epoch = 30
#hm_epoch = 125

for epoch in range(hm_epoch):
    l_total = 0
    
    for i in range(int(tNGX_train.shape[0]/batch_size)):
        _,l = sess.run([optimizer,loss],feed_dict={X: tNGX_train[i*batch_size:(i+1)*batch_size].toarray()})
        
        
        l_total += l
    print("The loss at : ",epoch," is : ",l_total)

The loss at :  0  is :  5.793243229389191
The loss at :  1  is :  5.021573752164841
The loss at :  2  is :  4.248348265886307
The loss at :  3  is :  3.4341687858104706
The loss at :  4  is :  2.582311287522316
The loss at :  5  is :  1.7669197916984558
The loss at :  6  is :  1.1181423477828503
The loss at :  7  is :  0.710472583770752
The loss at :  8  is :  0.4930123891681433
The loss at :  9  is :  0.37901427410542965
The loss at :  10  is :  0.31184341572225094
The loss at :  11  is :  0.253738833591342
The loss at :  12  is :  0.2007521754130721
The loss at :  13  is :  0.1573371607810259
The loss at :  14  is :  0.13592195324599743
The loss at :  15  is :  0.11877967324107885
The loss at :  16  is :  0.09995487844571471
The loss at :  17  is :  0.09222095273435116
The loss at :  18  is :  0.08863148931413889
The loss at :  19  is :  0.08588202437385917
The loss at :  20  is :  0.08358381735160947
The loss at :  21  is :  0.08162106527015567
The loss at :  22  is :  0.07992126513

In [26]:
# batch_train, y_train = mnist.train.next_batch(56000)
# batch_test, y_test = mnist.test.next_batch(14000)


# Encode and decode the digit image
encoded_train = sess.run(encoder_op, feed_dict={X: tNGX_train.toarray()})
encoded_test = sess.run(encoder_op, feed_dict={X: tNGX_test.toarray()})


In [10]:
#num_hidden_1 = 300
#num_hidden_2 = 200
#accuracy 0.7308666666666667
from sklearn.linear_model import LogisticRegression
from sklearn import metrics
logreg = LogisticRegression()
logreg.fit(encoded_train, tNGy_train)
# y_pred = logreg.predict(encoded_test)
print("accuracy",logreg.score(encoded_test,tNGy_test))
sess.close()


accuracy 0.7308666666666667


In [7]:
#num_hidden_1 = 400
#num_hidden_2 = 300
from sklearn.linear_model import LogisticRegression
from sklearn import metrics
logreg = LogisticRegression()
logreg.fit(encoded_train, tNGy_train)
# y_pred = logreg.predict(encoded_test)
print("accuracy",logreg.score(encoded_test,tNGy_test))
sess.close()

accuracy 0.7472


In [12]:
#num_hidden_1 = 500


from sklearn.linear_model import LogisticRegression
from sklearn import metrics
logreg = LogisticRegression()
logreg.fit(encoded_train, tNGy_train)
# y_pred = logreg.predict(encoded_test)
print("accuracy",logreg.score(encoded_test,tNGy_test))
sess.close()



accuracy 0.7577333333333334


In [17]:
#num_hidden_1 = 700


from sklearn.linear_model import LogisticRegression
from sklearn import metrics
logreg = LogisticRegression()
logreg.fit(encoded_train, tNGy_train)
# y_pred = logreg.predict(encoded_test)
print("accuracy",logreg.score(encoded_test,tNGy_test))
sess.close()




accuracy 0.7695333333333333


In [27]:
#num_hidden_1 = 100


from sklearn.linear_model import LogisticRegression
from sklearn import metrics
logreg = LogisticRegression()
logreg.fit(encoded_train, tNGy_train)
# y_pred = logreg.predict(encoded_test)
print("accuracy",logreg.score(encoded_test,tNGy_test))
sess.close()





accuracy 0.5556


In [19]:
from sklearn.metrics.pairwise import cosine_similarity
old_distance = cosine_similarity(tNGX_test.toarray())
new_distance = cosine_similarity(encoded_test)

In [20]:
for i in range(tNGX_test.shape[0]):
    old = np.argsort(-old_distance[i])
    new = np.argsort(-new_distance[i])
    print("old:",old[:20])
    print("new:",new[:20])

old: [    0 11184 13476 11946  8311 11312  2361  2867  7476  7330 13588  6760
  2289  4506  7142  6839  9968  5707  1803 11961]
new: [    0 11184 13476  2867 11946  8311  7476  2361  7330 11312  2289 13588
  7142  4506 11961 10188  5707  6760  1803 10344]
old: [    1 11766  4582  8486   777  1140  4132 13653  3751  8772 12907 13416
  3281   875  7423  1425  8005  7980  9712   456]
new: [    1 11766  4582   777  8486  1140 13653  8772  3751  4132  7980  3281
  1425   456   875  9998 12904  2855 13416 10416]
old: [    2 12577 10818  7747  5478 13813  7182  6514  1229 13170  1382 12748
 10241  7586 13039 12879  5777 10874  1784  3941]
new: [    2  7747 12577 10818  5478 13813  1229  7182 13170  6514 12748  1784
  5777  9368 10874 10241 13039   196 10537  5630]
old: [    3 14546  7145   152  6596  9160 12272 11260 13235  4166 13394  9056
  4379   793  1052  5015  9064  8379  9668  7990]
new: [    3 14546  7145   152  4166 11260  6596 12272 13394  5015  4379  9160
  9056  9064 13235  5814 1

old: [   91 11338    89  3630   248 14118  3253 11095   468 14774   367  6667
  2835  7683  4774 11641  6423  2771  3156  9897]
new: [   91 11338  3630 11641 14118  3156 14184  9019   279 12809 11095  6667
  6813 13707 12606  9727  4699  2771  4774  9897]
old: [   92  3199  9884 12408  2285 11971  5071  6226  5115 13294 14977   612
  5166  2381  6444  1941 10765 12254 11605 14840]
new: [   92  2285  6226   612 10765 13294  5115 12299 14174 12408  7053  7492
  6195  1377  4319  1585  7312  6603 11921  9733]
old: [   93  6045  9462  2183  2748  5943  4800 10928 11395 14212  3859  9192
  6189  6102  8438  6115  6361  2804  7808 10100]
new: [   93  8438 10928 11395  7808  2748  2183  6361  4781  9192   964  7882
 12657  5545 14584  9462  6852  1209  1365  9223]
old: [   94   188  2603 13621   731 12126  1214 12605  2193  1207  3251  8820
 11082  6508  7116 12879  4114 13698 12887  6958]
new: [   94   188 12605 12126  1214 11082  4114 14775 13621   731  9874  6508
  2193 14843 12887 11747 1

old: [11136  3916  6997   174  1105 11235 10578  4717  8043  5949  7786 10422
 11653   855   295 10447  6803  6684  4131  4518]
new: [  174  6997 11136  3916  1105 11235 10578  8043  7786 10422 11653  3988
  4518  4131 10447 12056  6684  2833  6803  6602]
old: [  175  4178 11357 14005  4657  1934  1688  1691   517  8426  5265  9007
 12320  4248  4020  8141 10671  6122 14679  7987]
new: [  175 11357 10671  8141  3887   517   660  4072 14449  7137 12137  6698
  7930  3356  3569   411 12713  2259  2929 12170]
old: [  176  3022  8319 14968 12467 10557  6427 10067  2636 10528  7896  1455
  3128 13887  5402  3146 12698  2016  8912 12863]
new: [  176  8319  7896  8071 12467 10528  2579  6292  1144  3146  4727 13444
 11061  5034 11833 13332   513  3128 10557  1455]
old: [  177 10079  8515 12357 14213  2074  6696 13761  2606  3084 11683 12844
  7099  1341  6142  7010  9991  7884  5774  3721]
new: [  177 10079  7099 12844 12357 11683  9991  6696  3084 13707 12727 14213
  7010  1341   419  6222 1

old: [  272 12251  3313  8527 12526 10655 14454  3352 10762   314 14999 14552
  6285 13686  7075  1358  1818 10666 11591 14894]
new: [  272 12251  3313  3352  8527 14454 12526 14999 14894 10655 10666  1358
   871  1114 10762  6285  1060  7523 11629  7191]
old: [  273  3929  1343 12444  7673 13320  7853  4478 10719   729 14711 14460
  5439 10766 14396  4594  2444  5423  6589 10213]
new: [  273 13320  5439 14711 10766  4722  7844  2444  9836  9188 11474   109
 11730 14460  2759  3778  1083  6695 14595  5799]
old: [  274 10989 12178  9486  4188  9138  2466 14586  9916  8961  2651  7172
 12153  1199 12558  1182  5945  8561  6181  5959]
new: [  274  2466 14586  2829 10490  1199 10385 13468  4714  5045 13624  6640
 10007 10811  4188 11462 14201 13832 11278 12659]
old: [  275 10167 12378  5500    58  5374  6805  5132  2632  5278   475 12797
 14271   278 13495   636  9357 12764  5279  3354]
new: [  275 12378  5278    58 14553 12797  8611 10359  8107   473  9112  5279
 13902 12607  5782  8547 1

old: [  367 11095  3148   248    89   468  3630 13195  6667    91 14774  6444
 14656  4774  7683  3199 11153   131  7264 14118]
new: [  367 11095  3148   131   248  1821  3630  3953 11153 14656  6444  6667
  1202  9276   612  7729  5486  2771  4190 12408]
old: [  368  7126  3612  7485    31 14332  2223  9406 10012 13696  7338  5878
 11196   320 10441 13375  8204   533 12584  5218]
new: [  368  7126  7485  3612    31  2223  9406 14332 13696 10012  7338  5878
 11196 10441   320 13375  8204 12584   533 12069]
old: [  369 14180  3080 11857 10250  4822  8185  5380 10471 13006 14480  5793
  6622  4335  1568 11177  8973 14169 11751  2300]
new: [  369 14180  3080 11857  4822  8185 10471  4335  9179 13849 13006 14169
  6622 10768  7602  5380  5793  7967   926  1710]
old: [  370 14760 11157 10333  1880  1702    84 12512  6502  3336 10280 11920
  4736  1684 11246  7457 14468 10186   101  7673]
new: [  370 14760 11157    84 10280  9836 10619  7161  8094  4898  1192 10852
  7143 13832 13505  4263  

...

old: [14605 13215 11621    25  1553   309 10302 10551  8588  6590  4340  9962
 14327  5513 13109   739  7305  5351  4725  3549]
new: [14605 13215 11621  8588  6590  9962    25 14327  4340  1553   309 10721
  5385  7083  6481 14274 10302 10551  7590  7305]
old: [14606  6942  1906  3832 10180  6069 11401 13004 14085  7087  9705 12779
  8583 10384  8057  4033  1604 14231 14637  8199]
new: [14606  6942 11401  6069  1906 14085  9705 10384 13004  8057 11893  2951
  3832   724  8625  1604 10022  8283  9713 10180]
old: [14607  4517  9684  2634 11501 12313   328  3157  5794  4707   604 11586
  7976   894  7810   400  4738 14622  9682 10977]
new: [14607  2634  4707 11586   894  7976  4738  9682  9487  7334  9684  1592
   328  5032   783  1884 13649  3722  6927  7329]
old: [14608 13996  4060  5395 14355  3984   739 13109 11175  4725  6330  5351
  7305  3549  8600 13697  2339 11330  4554  8714]
new: [14608 13996 14355 12026   556  7590  2496 12186  6481 10960 13321  4554
 10498  8626 11330  7000  

old: [14702  5522  1366  4455   403  9844  2741  8173  5011 13348  4761  2600
  9798 10546  9385  4350 13257 12516 13873  3961]
new: [14702  5522  1366  4455 14725  2600  6137 14447  4077  1298 13234  9349
   322  7806 13263  8283  3730  8501 13507 13440]
old: [14703  9204 14031 13665 12106  1680 14508 10754  1264  7088  6299 11200
  3145 14593  1492  1380  3434  3557  2351  3897]
new: [14703 14031  9204  7088  6299 13665 14593 14508 11200  1492 10754  1264
  3557  3145  1680  3434  1380 12106  1613  5831]
old: [14704  6157  3240 14369 12845  8419  1602  7398 10195  9663   464   757
  7794  4681 12644  3926 10177   645   254   618]
new: [14704 14369  1602  8419  6157   464   488  7794  3240   757 10195   999
  3662 14686 10177   645     5  9663  7398  9650]
old: [14705  9823 10448  6904  3048 14353 10899  3972  5080  2327  2447  5960
  6158  2924  3475  1353  8846  1251 11992   451]
new: [14705 10448 14353  3475  1353  1906  8846  8283  6158 13709  9705  8057
  2652 13547  1018  6143  

old: [14799 11604 13148  4179 10724 10244 14319  1919  6164  1628  2724 13493
  4841 11634  8042  2658  4935  1561  3388  6004]
new: [14799 11604  1628 10244 10724 13493  1561  6164 13148  9935 14308 14319
  4841  1919  3388  4179  2075  9216 11634 10380]
old: [14800  6770  8408  5131  3822  6612  1447  5072 13734  9539 12897 10992
 13018  9707  7626 12285 12047  5583 13355    60]
new: [14800  6770  8408  1447  5131 13734  5072  3822  6612 12047  9539 13018
  7626 13355 10992 10101  2273 14160 12955 14009]
old: [14801  6120 11530 12672 13052  4079  9174 11280 12737 11523  9647  6659
 12536 10275 13802  5139  1983  6201  6041   549]
new: [14801 11530  6120 10275  5139  6041  9174 12536 10086  9625  8192 12462
  5145  8253 12029  3034 12737  4557  4981  1811]
old: [14802 14014  5387 11293 13044  7675  1830  4084  5594  1577  3490  9872
  7645 13840  4751 13995  3765 12514  2907  2172]
new: [14802 14014 11293  7675  4751  9872  2172  1830  5594  3765  2109  2540
 12468  9708  7436  1577 1

old: [14897  2375  7240  5249  8970  3433  7468  7158 14823  1117  6018  5762
 10311   847  7517  2816  8892  9020  3452  2697]
new: [14897  8970  7468  1117  2375  8892  6018  3433  5249   847 10311  7517
  7240  9020  2816  9111 14823 13903 10462  6985]
old: [14898  6540 11651   244  7418 14740  4032  5108  8202 11070  2147 13431
  7286  9842 12293 11526  5343  5754  5813 14524]
new: [14898  6540  2147  7418  7286 11070  9842  4032  5108 14920 13236  5813
  4145 12755 12086  1699 11526 10267  7708  5754]
old: [14899  7303  2496 14333  7305  3549 13109   739 11175  4725  5351  6330
  8600  1072  4060  2339  4554  3984   556  5158]
new: [14899  7305  1072   606  2496  3905  2574  3569 14019  5860 13383 14648
  8540  8843  6083  5540  5458 14910  8358  6443]
old: [14900   860  4987 10633   371  5007  6155  1431  9382 12084  7933  9765
  9096  3901  5103 11475  2704  1950  4627  9597]
new: [14900  4987  1431   371  9382  1950  2972  5135 10616  4083 14378  5302
  7922  2659  7534  6498  

old: [14988  6845 12878 11528  6734  9491   862  7068  7526 10215  1334 10194
  1536  4297 14712 12761  6376  9137   441  5643]
new: [14988 11528  6734 12878   862 10215  9491 10194  6845  7526  7068  1168
  4297 14376  8534  5643   441 12761  3043  9137]
old: [    0  9992  9993  9994  9995  9996  9997  9998  9999 10000 10001 10002
 10003 10004 10005 10006 10007 10008 10009 10010]
new: [ 2941 11334  4919  4165 13911 14846 13912  9939 12465  3323 12821 13915
  3317  2893  7953  8343 12403  2217  4902  8592]
old: [14990  3234  8906  1073  9614  9946 12247  2576  6324  3720  9622  5552
  5592  7090   540  2996  4932  2315 11370 10475]
new: [14990  1073  9614  9946  3234  5592  9622  3720 10475  2576  2996 11985
  4932 14569 11370  7090  2315 11581 13833   230]
old: [14991  7156  6484 14535 10725  2270 10165  9120  9476  9956  9414  6133
  6982  6327  4512  4940  6714 12528  7174 11098]
new: [14991 10725  6327  9956  9414  4512  9120  6133 13012  2444  2270  6484
 13895 13889 11739 14096 1

In [18]:
from sklearn.linear_model import LogisticRegression
from sklearn import metrics
logreg = LogisticRegression()
logreg.fit(tNGX_train, tNGy_train)
y_pred = logreg.predict(tNGX_test)
print("accuracy",metrics.accuracy_score(tNGy_test, y_pred))

accuracy 0.7425333333333334
